<a href="https://colab.research.google.com/github/alexlautw9527/for_notebook/blob/main/folium_brn.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [42]:
import folium
from folium import plugins

In [2]:
import pandas as pd
import numpy as np

In [3]:
!pip install geopandas -q

     |████████████████████████████████| 1.0 MB 5.2 MB/s 
     |████████████████████████████████| 6.3 MB 35.8 MB/s 
     |████████████████████████████████| 16.7 MB 437 kB/s 


In [26]:
import json
import geopandas as gpd

# 打點資料整理

In [6]:
# 競行
comp_brn_df = pd.read_csv('/content/drive/MyDrive/03_RESOURCE/GIS/競行分佈_台中市_整合.csv', encoding = 'CP950')

# 科學園區點位
sci_ind_df = pd.read_csv('/content/drive/MyDrive/03_RESOURCE/GIS/科學園區與工業區地址.csv', encoding = 'CP950')

# 打點後地址
all_xy_df = pd.read_csv('/content/drive/MyDrive/03_RESOURCE/GIS/競行與科學園區打點csv.csv', encoding = 'CP950')

sci_ind_df.columns = ['seq_no', 'park_nm', 'mng_nm', 'addr', 'area']
comp_brn_df.columns = ['seq_no','bank','brn_nm','dist', 'addr']

In [7]:
# 單純用時間區分批次
comp_brn_xy = all_xy_df[all_xy_df['UPLD_TM']==100505]
sci_ind_xy = all_xy_df[all_xy_df['UPLD_TM']==100447]

In [8]:
comp_brn_df = comp_brn_df.merge(comp_brn_xy[['SEQ_NO','X','Y','LVL']], left_on ='seq_no', right_on = 'SEQ_NO')
sci_ind_df = sci_ind_df.merge(sci_ind_xy[['SEQ_NO','X','Y','LVL']], left_on ='seq_no', right_on = 'SEQ_NO')

In [9]:

# 依分行填上icon url
icon_url_list = list(zip(['台北富邦', '中國信託', '國泰世華', '玉山商銀'], 
    ['https://upload.wikimedia.org/wikipedia/zh/thumb/7/70/Fubon_Group.svg/1200px-Fubon_Group.svg.png',
     'https://media.cakeresume.com/image/upload/s--PdvYj5lM--/c_pad,fl_png8,h_400,w_400/v1564465077/jaahzogkgdfd5ydubryd.png',
     'https://upload.wikimedia.org/wikipedia/zh/thumb/2/24/New_Lin_Yuan.svg/1200px-New_Lin_Yuan.svg.png',
     'https://upload.wikimedia.org/wikipedia/commons/thumb/5/52/E.SUN_Bank.svg/800px-E.SUN_Bank.svg.png',
     ])
)

# 打點精確度太低的手動填上
comp_brn_df.loc[comp_brn_df['LVL']>1, 'X'] = 120.64990836891074
comp_brn_df.loc[comp_brn_df['LVL']>1, 'Y'] = 24.154341279320384

for i in icon_url_list:
  comp_brn_df.loc[comp_brn_df['bank']==i[0], 'icon_url'] = i[1]
  
comp_brn_df = comp_brn_df.loc[comp_brn_df['bank']!='台新銀行', :]

In [10]:
# 打點精確度太低的手動填上

sci_ind_df.loc[sci_ind_df.LVL>1, 'X'] = 120.71404820939352
sci_ind_df.loc[sci_ind_df.LVL>1, 'Y'] = 24.095284200618924

In [33]:
comp_brn_df.head(3)

seq_no  bank brn_nm dist                     addr  SEQ_NO           X  \
13      14  台北富邦   中港分行   西區    臺中市西區臺灣大道二段218號1樓、2 樓      14  120.669116   
14      15  台北富邦   豐原分行  豐原區      臺中市豐原區向陽路139號1、2、3樓      15  120.725199   
15      16  台北富邦   台中分行   西區  臺中市西區柳川西路二段196號1、2、3、8樓      16  120.674998   

            Y  LVL                                           icon_url  
13  24.152124    1  https://upload.wikimedia.org/wikipedia/zh/thum...  
14  24.252383    1  https://upload.wikimedia.org/wikipedia/zh/thum...  
15  24.141752    1  https://upload.wikimedia.org/wikipedia/zh/thum...

In [34]:
sci_ind_df.head(3)

seq_no     park_nm       mng_nm               addr       area  SEQ_NO  \
0       1       台中工業區  工業局中區工業區管理處  台中市西屯區協和里工業區五路2號?      583公頃       1   
1       2  中部科學園區台中園區   國科會科學園區管理局        台中市西屯區中科路2號      466公頃       2   
2       3     大甲幼獅工業區  工業局中區工業區管理處   台中市大甲區日南里幼獅路36號?  218.47 公頃       3   

            X          Y  LVL  
0  120.607906  24.168780    1  
1  120.618795  24.209706    1  
2  120.651709  24.404585    1

In [11]:
atm_df = pd.read_csv('/content/drive/MyDrive/03_RESOURCE/GIS/atm_點位.csv', encoding = 'CP950')

# 分行資料整理

In [12]:
## 各分行地址與基本資訊
brn_df = pd.read_csv('/content/drive/MyDrive/03_RESOURCE/GIS/taishin_brn.csv').drop_duplicates()

## 分行地址與點位
brn_xy_df = pd.read_csv('/content/drive/MyDrive/03_RESOURCE/GIS/brn_xy_df.csv')

## 合併並去掉重複
brn_df = brn_df.merge(brn_xy_df,how='left' ,on = 'addr').copy()
brn_df = brn_df.drop_duplicates()

In [13]:
tc_brn_df = brn_df[brn_df['country'] =='台中市']

In [ ]:
tc_brn_df.loc[:,['lat', 'lon']] = tc_brn_df.loc[:,['lat', 'lon']].astype(float)

In [18]:
tc_brn_df[0:3]

brn             addr               tel  cd  ins_box country        lat  \
6   台中分行  台中市西區台灣大道2段416號  電話：(04)2328-5577   7  保險箱業務：有     台中市  24.155266   
19  大里分行  台中市大里區中興路二段127號  電話：(04)2483-4088  18  保險箱業務：有     台中市  24.104291   
24  豐原分行   台中市豐原區圓環東路368號  電話：(04)2525-7999  22  保險箱業務：有     台中市  24.244898   

           lon  
6   120.663853  
19  120.688566  
24  120.724200

In [21]:
# 轉tuple

tc_brn_list = list(tc_brn_df[['brn', 'lat', 'lon']].to_records(index=False))

In [22]:
tc_brn_list[0:3]

[('台中分行', 24.155266, 120.663853),
 ('大里分行', 24.104291, 120.688566),
 ('豐原分行', 24.244898, 120.7242)]

# 行政區域界限與捷運點位處理

[行政區界線資料](https://sheethub.com/ronnywang/%E9%84%89%E9%8E%AE%E5%B8%82%E5%8D%80%E8%A1%8C%E6%94%BF%E5%8D%80%E5%9F%9F%E7%95%8C%E7%B7%9A)

In [27]:
tw_geo = gpd.read_file("/content/drive/MyDrive/03_RESOURCE/GIS/鄉鎮市區行政區域界線.json")

In [28]:
# 取出台中市界線
tc_geo_df = tw_geo[tw_geo['C_Name'] == '臺中市']

In [ ]:
!wget https://data.moi.gov.tw/MoiOD/System/DownloadFile.aspx?DATA=6684962F-C0ED-4D47-A31A-B1732BEDA50B -O mrt.zip

In [31]:
!unzip -O CP950 /content/mrt.zip

Archive:  /content/mrt.zip
  inflating: MARK_捷運車站_1101208.dbf  
  inflating: MARK_捷運車站_1101208.prj  
  inflating: MARK_捷運車站_1101208.shp  
  inflating: MARK_捷運車站_1101208.shx  
  inflating: Metadata.xml            


In [32]:
mrt_geo = gpd.read_file("/content/MARK_捷運車站_1101208.shp",encoding='UTF8')

# TWD97轉換WGS84
mrt_geo = mrt_geo.to_crs(epsg=4326)

# 篩掉出入口(只剩總站) 篩選台中 
mrt_geo = mrt_geo[(~mrt_geo['MARKNAME1'].str.contains('出入口') & mrt_geo['MARKNAME1'].str.contains('臺中'))]
mrt_geo['order'] = mrt_geo['MARKNAME1'].str.extract('(\d+)').astype(int)
mrt_geo = mrt_geo.sort_values('order')

In [23]:
poten_df = pd.read_csv('/content/drive/MyDrive/03_RESOURCE/GIS/台中各區潛力值.csv', encoding = 'CP950')
poten_df.head()

DIST  SCORE
0  西屯區      5
1  北屯區      5
2   西區      5
3  南屯區      4
4   北區      4

In [36]:
# 併入潛力分數
tc_geo_df = tc_geo_df.merge(poten_df, left_on='T_Name', right_on='DIST')

In [37]:
import branca
import random

# 開始建立地圖
[folium地圖介面功能](https://github.com/python-visualization/folium/blob/main/examples/Plugins.ipynb)

In [40]:
%%capture


# map
map_with_subgroups = folium.Map(
    
    # 台中市
    location=[24.148260576435973, 120.68632889393434],
    zoom_start=13,
    tiles="OpenStreetMap"
)

# all subgroups
all_subgroups = folium.FeatureGroup(name='all')
map_with_subgroups.add_child(all_subgroups)


In [43]:
%%capture
# subgroup 1
atm_group = plugins.FeatureGroupSubGroup(all_subgroups, 'ATM')
sci_group = plugins.FeatureGroupSubGroup(all_subgroups, '科學園區')
comp_brn_group = plugins.FeatureGroupSubGroup(all_subgroups, '競行')
mrt_group = plugins.FeatureGroupSubGroup(all_subgroups, '捷運')
km1_group = plugins.FeatureGroupSubGroup(all_subgroups, '台新分行周圍1km')
#move_group = plugins.FeatureGroupSubGroup(all_subgroups, '沙鹿分行遷址據點')


map_with_subgroups.add_child(atm_group)
map_with_subgroups.add_child(sci_group)
map_with_subgroups.add_child(comp_brn_group)
map_with_subgroups.add_child(mrt_group)
map_with_subgroups.add_child(km1_group)
#map_with_subgroups.add_child(move_group)

## 畫區域界線

In [44]:
colorscale = branca.colormap.linear.GnBu_09.scale(0, 5) 

In [45]:
colorscale = colorscale.to_step(index=[1-0.1,
                                       2-0.1,
                                       3-0.1,
                                       4-0.1,
                                       5-0.1,
                                       6-0.1])

In [47]:
# 後續依區域潛力分數上色
colorscale

In [ ]:
for i in range(1,6) :
  print(colorscale(i))

#f7fcf0ff
#ccebc5ff
#7bccc4ff
#2b8cbeff
#084081ff


In [58]:
r = list(tc_geo_df.iterrows())[1][1]
geo_j = gpd.GeoDataFrame(
        {
         'geometry':[r['geometry']], 
         'SCORE': [r['SCORE']]
        }
         ).to_json()

In [63]:
# 從每一次遍歷產生的geojson確定score去哪裡取
#["properties"]["SCORE"]
geo_j

'{"type": "FeatureCollection", "features": [{"id": "0", "type": "Feature", "properties": {"SCORE": 3}, "geometry": {"type": "Polygon", "coordinates": [[[120.693907342, 24.15250209], [120.693994691, 24.152490599], [120.694086008, 24.15249285], [120.694231009, 24.15248979], [120.694452325, 24.152489186], [120.694576982, 24.15246456], [120.694641399, 24.152425782], [120.694728281, 24.152384411], [120.694874119, 24.152354897], [120.694996564, 24.152348696], [120.695158403, 24.152302897], [120.695389406, 24.152202158], [120.695571012, 24.152141147], [120.695759319, 24.152108791], [120.695954202, 24.152097036], [120.696135368, 24.152087762], [120.696226145, 24.152055529], [120.696466168, 24.151971907], [120.696725634, 24.151852414], [120.696985136, 24.151735205], [120.697192212, 24.151703743], [120.697451563, 24.151656655], [120.697614247, 24.15166486], [120.697793764, 24.151630317], [120.697962959, 24.151575212], [120.698118131, 24.151503059], [120.698127851, 24.151499464], [120.698482392, 

In [65]:
for _, r in tc_geo_df.iterrows():
    # Without simplifying the representation of each borough,
    # the map might not be displayed
    #sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    geo_j = gpd.GeoDataFrame(
        {
         'geometry':[r['geometry']], 
         'SCORE': [r['SCORE']]
        }
         ).to_json()
    

    style_function = lambda x: {
        # 從score決定顏色
        "fillColor":colorscale(x['properties']['SCORE']), 
        "fillOpacity":.7,
        'color':'gray', 
        'weight':0.8
    }
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=style_function)
    
    word = "{}: 潛力分數{}".format(r['T_Name'],str(r['SCORE']))
    iframe = folium.IFrame(word,
                       width=200,
                       height=50)
    popup = folium.Popup(iframe)


    popup.add_to(geo_j)
    geo_j.add_to(all_subgroups)

# 畫台新分行

In [66]:

## icon
for brn in tc_brn_list:
    icon = folium.features.CustomIcon('https://upload.wikimedia.org/wikipedia/zh/thumb/b/b2/Taishin.svg/150px-Taishin.svg.png', icon_size=(23, 23))
    iframe = folium.IFrame(brn[0],
                       width=200,
                       height=50)
    popup = folium.Popup(iframe)
    folium.Marker(
        popup = popup,
        location=[brn[1], brn[2]],
        #icon=folium.Icon(color="red",icon='fa-university', prefix='fa')
        icon=icon
        
).add_to(all_subgroups)

## 一公里範圍
for brn in tc_brn_list:
    folium.Circle(
        radius=1000,
        fill_opacity=0.35,
        location=[brn[1], brn[2]],
        weight=0,
        color="#E34236",
        fill_color="#FF6562",

).add_to(km1_group)

## 畫台新atm點位


In [67]:
for _, atm in atm_df.iterrows():
    folium.Circle(
        location=[atm['Y'], atm['X']],
        radius=30,
        color="#BA3F20",
        weight=1,
        fill_color="#BA3F20",
        fill_opacity=1
        
).add_to(atm_group)

## 畫競行點位

In [68]:
for _, brn in comp_brn_df.iterrows():
    icon = folium.features.CustomIcon(brn['icon_url'], icon_size=(20, 20))
    iframe = folium.IFrame(brn['brn_nm'],
                       width=200,
                       height=50)
    popup = folium.Popup(iframe)
    folium.Marker(
        popup = popup,
        location=[brn['Y'], brn['X']],
        #icon=folium.Icon(color="red",icon='fa-university', prefix='fa')
        icon=icon
        
).add_to(comp_brn_group)

## 畫科學園區工業區

In [69]:
for _, r in sci_ind_df.iterrows():
    iframe = folium.IFrame(r['park_nm'],
                       width=200,
                       height=50)
    popup = folium.Popup(iframe)
    folium.Marker(
        popup = popup,
        location=[r['Y'], r['X']],
        icon=folium.Icon(color="gray",icon='fa-industry', prefix='fa')
    ).add_to(sci_group)


# 畫捷運點位

In [71]:
# 先得到座標list 方便畫線
mrt_point=[]
for _, r in mrt_geo.iterrows():
    sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    mrt_point.append([float(sim_geo.y), float(sim_geo.x)])
         


In [72]:
for _, r in mrt_geo.iterrows():    
  sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)

  iframe = folium.IFrame(r['MARKNAME2'],
                       width=200,
                       height=50)
  popup = folium.Popup(iframe)
  folium.Marker(
      popup = popup,
      location=[float(sim_geo.y), float(sim_geo.x)],
      #icon=folium.Icon(color="red",icon='fa-university', prefix='fa')
      icon=folium.Icon(color="green",icon='fa-subway', prefix='fa')
        
).add_to(mrt_group)

In [73]:
folium.PolyLine(mrt_point, color='#5BBA39', weight = 3).add_to(mrt_group)

## 遷移

In [ ]:
iframe = folium.IFrame('沙鹿分行遷址據點',
                  width=200,
                  height=50)
popup = folium.Popup(iframe)

folium.Marker(
      popup = popup,
      
      location=[float(24.1727917237235), float(120.678719605285)],
      #icon=folium.Icon(color="red",icon='fa-university', prefix='fa')
      icon=folium.Icon(color="red",icon='fa-university', prefix='fa')
        
).add_to(move_group)

## 一公里範圍
folium.Circle(
    radius=1000,
    fill_opacity=0.35,
    location=[float(24.1727917237235), float(120.678719605285)],
    weight=0,
    color="#E34236",
    fill_color="#FF6562",

).add_to(move_group)


In [74]:
# add layer control to map (allows layers to be turned on or off)
folium.LayerControl(collapsed=False).add_to(map_with_subgroups)


In [75]:
# display map
map_with_subgroups

In [ ]:
map_with_subgroups.save('台中分行地圖分布_FNL.html')